In [6]:
import streamlit as st
import pandas as pd
import numpy as np
import plotly.express as px


1. Import the data and take a look

In [39]:
data = pd.read_csv("../vehicles_us.csv")
data.sample(10)

price  model_year                       model  condition  cylinders  \
2239    5900      2012.0                jeep liberty       good        6.0   
16286   9995      2009.0               honda odyssey       good        6.0   
40260   1495      2004.0                 ford taurus       good        6.0   
26940   7200         NaN            hyundai santa fe   like new        4.0   
36657   3500      2007.0    chevrolet silverado 1500       good        8.0   
27305   4800         NaN  chevrolet silverado 2500hd       good        8.0   
619    18900      2019.0             toyota camry le   like new        4.0   
39113  26000      2017.0    ford mustang gt coupe 2d       good        8.0   
50241   5500      2010.0            chevrolet malibu       good        4.0   
11832  27500         NaN           toyota highlander  excellent        6.0   

         fuel  odometer transmission    type paint_color  is_4wd date_posted  \
2239      gas  145795.0    automatic     SUV         NaN     NaN  2019-02-27   
16286     gas   68768.0    automatic     van       white     NaN  2018-07-17   
40260     gas  125023.0       manual   sedan        grey     NaN  2018-05-20   
26940     gas     109.0    automatic     SUV        blue     1.0  2018-09-05   
36657     gas  185000.0       manual   truck       white     NaN  2018-07-29   
27305  diesel  318000.0    automatic  pickup       white     NaN  2019-02-01   
619       gas   13355.0    automatic   sedan       white     NaN  2019-02-09   
39113     gas   33528.0        other   coupe      yellow     NaN  2018-06-01   
50241     gas  141500.0    automatic   sedan       white     NaN  2018-09-29   
11832     gas    6464.0    automatic     SUV       brown     1.0  2019-02-10   

       days_listed  
2239            36  
16286           82  
40260           59  
26940           14  
36657           34  
27305           85  
619             55  
39113           47  
50241           40  
11832           10

In [40]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


In [41]:
data.duplicated().sum()


0

In [42]:
data["condition"].unique()

array(['good', 'like new', 'fair', 'excellent', 'salvage', 'new'],
      dtype=object)

In [11]:
data["fuel"].unique()

array(['gas', 'diesel', 'other', 'hybrid', 'electric'], dtype=object)

In [12]:
data["transmission"].unique()

array(['automatic', 'manual', 'other'], dtype=object)

In [13]:
data["type"].unique()

array(['SUV', 'pickup', 'sedan', 'truck', 'coupe', 'van', 'convertible',
       'hatchback', 'wagon', 'mini-van', 'other', 'offroad', 'bus'],
      dtype=object)

In [14]:
data["paint_color"].unique()

array([nan, 'white', 'red', 'black', 'blue', 'grey', 'silver', 'custom',
       'orange', 'yellow', 'brown', 'green', 'purple'], dtype=object)

There are no duplicates in this data set and all values in cateory columns are correct. no mispellings or duplicates.

2. Start planning EDA for this file with some key take aways in mind:

2a. initial thoughts for data frame clean up:
1. model year should be type int: error message "cannot convert nan to type int" --> I switched nan to 0 then made the swtich: done
2. we should split the model and type so we can sort by manufacturer: done
3. cylinders should be type int: error message "cannot convert nan to type int" --> I switched nan to 0 then made the swtich: done
4. check each column to make sure the values are unique and ther are no mistakes: done
5. potentially change nan to 0 for is_4wd. should also be type int --> I switched nan to 0 then made the swtich: done
6. change date posted to datetime type: done



2b. Change date_posted column to datetime type:

In [43]:
data["date_posted"] = pd.to_datetime(data["date_posted"], format = "%Y-%m-%d")
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   price         51525 non-null  int64         
 1   model_year    47906 non-null  float64       
 2   model         51525 non-null  object        
 3   condition     51525 non-null  object        
 4   cylinders     46265 non-null  float64       
 5   fuel          51525 non-null  object        
 6   odometer      43633 non-null  float64       
 7   transmission  51525 non-null  object        
 8   type          51525 non-null  object        
 9   paint_color   42258 non-null  object        
 10  is_4wd        25572 non-null  float64       
 11  date_posted   51525 non-null  datetime64[ns]
 12  days_listed   51525 non-null  int64         
dtypes: datetime64[ns](1), float64(4), int64(2), object(6)
memory usage: 5.1+ MB


2c. Split the Make and model for car:

In [44]:

def get_make(car):
    return car.split(' ')[0]

def get_model(car):
    info  = car.split(' ')
    return ' '.join(info[1:])

data['vehicle_make'] = data['model'].apply(get_make)
data['vehicle_model'] =  data['model'].apply(get_model)

In [17]:
data.head(10)

price  model_year           model  condition  cylinders fuel  odometer  \
0   9400      2011.0          bmw x5       good        6.0  gas  145000.0   
1  25500         NaN      ford f-150       good        6.0  gas   88705.0   
2   5500      2013.0  hyundai sonata   like new        4.0  gas  110000.0   
3   1500      2003.0      ford f-150       fair        8.0  gas       NaN   
4  14900      2017.0    chrysler 200  excellent        4.0  gas   80903.0   
5  14990      2014.0    chrysler 300  excellent        6.0  gas   57954.0   
6  12990      2015.0    toyota camry  excellent        4.0  gas   79212.0   
7  15990      2013.0     honda pilot  excellent        6.0  gas  109473.0   
8  11500      2012.0     kia sorento  excellent        4.0  gas  104174.0   
9   9200      2008.0     honda pilot  excellent        NaN  gas  147191.0   

  transmission    type paint_color  is_4wd date_posted  days_listed  \
0    automatic     SUV         NaN     1.0  2018-06-23           19   
1    automatic  pickup       white     1.0  2018-10-19           50   
2    automatic   sedan         red     NaN  2019-02-07           79   
3    automatic  pickup         NaN     NaN  2019-03-22            9   
4    automatic   sedan       black     NaN  2019-04-02           28   
5    automatic   sedan       black     1.0  2018-06-20           15   
6    automatic   sedan       white     NaN  2018-12-27           73   
7    automatic     SUV       black     1.0  2019-01-07           68   
8    automatic     SUV         NaN     1.0  2018-07-16           19   
9    automatic     SUV        blue     1.0  2019-02-15           17   

  vehicle_make vehicle_model  
0          bmw            x5  
1         ford         f-150  
2      hyundai        sonata  
3         ford         f-150  
4     chrysler           200  
5     chrysler           300  
6       toyota         camry  
7        honda         pilot  
8          kia       sorento  
9        honda         pilot

2d. Change apllicable columns to type int:

In [45]:
#data["model_year"] =  data["model_year"].fillna(0).astype("int")
data["cylinders"] =  data["cylinders"].fillna(0).astype("int")
data["is_4wd"] =  data["is_4wd"].fillna(0).astype("int")

#data["model_year"] = data["model_year"].fillna(0, np.nan)
#data["cylinders"] = data["cylinders"].fillna(0, np.nan)

data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 15 columns):
 #   Column         Non-Null Count  Dtype         
---  ------         --------------  -----         
 0   price          51525 non-null  int64         
 1   model_year     47906 non-null  float64       
 2   model          51525 non-null  object        
 3   condition      51525 non-null  object        
 4   cylinders      51525 non-null  int32         
 5   fuel           51525 non-null  object        
 6   odometer       43633 non-null  float64       
 7   transmission   51525 non-null  object        
 8   type           51525 non-null  object        
 9   paint_color    42258 non-null  object        
 10  is_4wd         51525 non-null  int32         
 11  date_posted    51525 non-null  datetime64[ns]
 12  days_listed    51525 non-null  int64         
 13  vehicle_make   51525 non-null  object        
 14  vehicle_model  51525 non-null  object        
dtypes: datetime64[ns](1

In [46]:
data.sample(10)

price  model_year                         model  condition  cylinders  \
12338   5200         NaN           chevrolet silverado       good          6   
8535   11500      2014.0                   kia sorento       good          4   
51410   9300      2016.0                    ford focus  excellent          0   
7165    9595      2011.0      chevrolet silverado 1500   like new          8   
18466   2400      2003.0                  honda accord   like new          6   
8254   38000      2015.0                      ram 3500       good          6   
22370  12677      2015.0                 jeep cherokee  excellent          4   
12319   1250      2008.0                  nissan versa       good          4   
14759      1      2018.0                   ford fusion  excellent          4   
45222  24200      2018.0  chevrolet camaro lt coupe 2d       good          6   

         fuel  odometer transmission       type paint_color  is_4wd  \
12338     gas  109345.0    automatic      truck      silver       1   
8535      gas  102578.0    automatic        SUV       black       0   
51410     gas       NaN    automatic      sedan      silver       0   
7165      gas  239950.0    automatic      truck        blue       1   
18466     gas   20000.0    automatic      sedan        grey       0   
8254   diesel   49000.0    automatic     pickup       white       1   
22370     gas       NaN    automatic        SUV         NaN       0   
12319     gas  296000.0    automatic  hatchback       white       0   
14759     gas   12500.0    automatic      sedan        blue       1   
45222     gas       NaN        other      coupe         NaN       0   

      date_posted  days_listed vehicle_make       vehicle_model  
12338  2018-05-03           21    chevrolet           silverado  
8535   2019-03-15           92          kia             sorento  
51410  2018-09-24           53         ford               focus  
7165   2019-02-25           15    chevrolet      silverado 1500  
18466  2018-05-19           52        honda              accord  
8254   2019-02-06           43          ram                3500  
22370  2018-07-24           35         jeep            cherokee  
12319  2018-12-05           30       nissan               versa  
14759  2018-05-04           51         ford              fusion  
45222  2018-11-23           24    chevrolet  camaro lt coupe 2d

initial thoughts for data visualization
1. most common make of car for sale: hist
2. avg price of car vs model year: scatter
3. color of cars: hist
4. car miles vs price by car make?: scatter
5. days listed vs car make
6. model of most popular make
7. type of car :hist



In [55]:

display(data["vehicle_make"].sort_values().unique())

common_make = data.groupby("vehicle_make")["price"].count()
display(common_make)


array(['acura', 'bmw', 'buick', 'cadillac', 'chevrolet', 'chrysler',
       'dodge', 'ford', 'gmc', 'honda', 'hyundai', 'jeep', 'kia',
       'mercedes-benz', 'nissan', 'ram', 'subaru', 'toyota', 'volkswagen'],
      dtype=object)

vehicle_make
acura              236
bmw                267
buick              271
cadillac           322
chevrolet        10611
chrysler           838
dodge             1255
ford             12672
gmc               2378
honda             3485
hyundai           1173
jeep              3281
kia                585
mercedes-benz       41
nissan            3208
ram               3316
subaru            1272
toyota            5445
volkswagen         869
Name: price, dtype: int64

1. Top 3 type of car and price: 
top 3 type of car is 1. SUV, 2. Truck, 3. Sedan

In [56]:
car_type_count = data.groupby("type")["price"].count().sort_values(ascending= False)
display(car_type_count)

type
SUV            12405
truck          12353
sedan          12154
pickup          6988
coupe           2303
wagon           1541
mini-van        1161
hatchback       1047
van              633
convertible      446
other            256
offroad          214
bus               24
Name: price, dtype: int64

In [34]:
fig = px.histogram(data, x=data["vehicle_make"], title = "Most Common Vehicle Make and Type For Sale", color = data["type"])
fig.show()

In [57]:
df_suv = data[data["type"] == "SUV"]
df_truck = data[data["type"] == "truck"]
df_sedan = data[data["type"] == "sedan"]

In [30]:
fig = px.histogram(df_suv, x ="price", nbins= 300, color = "vehicle_make")
fig.show()

In [31]:
fig = px.histogram(df_truck, x ="price", nbins= 300, color = "vehicle_make")
fig.show()

In [32]:
fig = px.histogram(df_sedan, x ="price", nbins= 300, color = "vehicle_make")
fig.show()

In [50]:
fig = px.scatter(data, x= "model_year", y = "price", color = "vehicle_make")
fig.show()


In [58]:
fig= px.scatter(df_suv, x= "model_year", y= "days_listed", color= "price")
fig.show()

In [59]:
plt.figure(figsize = (10,10))
plt.bar( x = data["type"], height = data["price"], color = "blue", alpha = 0.5)

plt.xlabel("Vehicle Type")
plt.ylabel("Price")
plt.title("Vehicle Type vs Vehicle Price")
plt.show()

st.header("Sprint 4 Project")
st.write(data.head)

NameError: name 'plt' is not defined

In [67]:
aesthetic = px.histogram(data, x= "model_year", color= "paint_color")
aesthetic.show()

In [ ]:
car_use = px.scatter(data, x="odometer", y= "model_year", color= "vehicle_make")
car_use.show()